In [2]:
from flightanalysis import Section, get_schedule, FCJson

with open("/home/tom/Documents/AutoJudge/fc_jsons/manual_F3A_P23_21_10_23_00000117.json", "r") as f:
    fcj = FCJson.parse_fc_json(f)

In [16]:
import numpy as np
import pandas as pd
from scipy import integrate
import plotly.express as px

fcj_aligned = fcj.schedule.get_subset(fcj.sec, 0, 17)
sec = fcj_aligned.remove_labels()

sched = get_schedule(fcj.schedule.category, fcj.schedule.name)

distance = sec.y.mean()
speed = sec.bvx.mean()
print("distance = {}, speed = {}".format(distance,1.2* speed))
template = sched.scale_distance(distance).create_raw_template(sec[0].direction, speed, distance)

from flightanalysis.schedule.elements import get_rates

ar_m_template = sched.match_rates(get_rates(sec)).create_raw_template(sec[0].direction, speed, distance)


distance = 212.21233999758022, speed = 31.553296819362746


In [24]:
from fastdtw import fastdtw
from scipy.spatial.distance import euclidean
from geometry import Points, Point


def get_brv(sec):
    brv = sec.gbrvel
    brv.data[:,0] = abs(brv.data[:,0])
    brv.data[:,2] = abs(brv.data[:,2])
    return brv


def align(tp, fl):
    return fastdtw(
        tp.data,
        fl.data,
        radius=5,
        dist=euclidean
    )


def copy_labels(template, flown, path):
    mans = pd.DataFrame(path, columns=["template", "flight"]).set_index("template").join(
            template.data.reset_index().loc[:, ["manoeuvre", "element"]]
        ).groupby(['flight']).last().reset_index().set_index("flight")

    return Section(flown.data.reset_index().join(mans).set_index("time_index"))


brvfl = get_brv(sec)
brvtp = get_brv(ar_m_template)

norms = max(brvfl.abs().max(), brvtp.abs().max())
brvflnorm = brvfl.whiten() * Point(1, 1, 0.1)
brvtpnorm = brvtp.whiten() * Point(1, 1, 0.1)




In [25]:
dist, path = align(brvflnorm, brvtpnorm)

align_vals = copy_labels(ar_m_template, sec, path)


In [26]:
from flightplotting.plots import plotdtw, plotsec


plotdtw(align_vals, sched.manoeuvres)#[0].elements)

no data for manoeuvre fight, Section created with empty dataframe
no data for manoeuvre tri, Section created with empty dataframe
no data for manoeuvre shark, Section created with empty dataframe
no data for manoeuvre loop, Section created with empty dataframe
no data for manoeuvre Landing, Section created with empty dataframe


In [27]:

from scipy import signal
from scipy.cluster.vq import whiten


px.line(brvflnorm.to_pandas()).show()
px.line(brvtpnorm.to_pandas()).show()
